In [1]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import odeint, solve_ivp
import math
import pypower
from pypower.api import case9, ppoption, runpf, printpf
from copy import deepcopy

import pandas as pd


def dx_dt(x, t, fault_time, Y, V0, Pm, M):
    ps = 0

    for k in range(len(fault_time)):
        if t > fault_time[k]:
            ps = k + 1

    if t > 1:
        a = 0

    Ybus = Y[ps]
    Vg = V0 * np.exp(1j * x[0:3])
    Ibus = np.matmul(Ybus, Vg)
    S = np.conj(Ibus) * Vg
    Pe = np.real(S)
    dx = x[3:6]
    return np.hstack([dx, (Pm - Pe) / M])


def CalYbus(branch):
    Nbus = int(max([max(branch[:, 0]), max(branch[:, 1])]))
    Nbranch = len(branch[:, 0])
    Ybus = np.zeros([Nbus, Nbus])
    Ybus = np.complex_(Ybus)
    for k in range(Nbranch):
        N1 = int(branch[k, 0] - 1)
        N2 = int(branch[k, 1] - 1)
        YY = 1/(branch[k, 2]+1j*branch[k, 3])
        tap = branch[k, 8]
        if tap == 0:
            tap = 1

        tap = 1/tap
        Ybus[N1, N1] = Ybus[N1, N1] + tap * tap * YY + 1j * branch[k, 4]
        Ybus[N2, N2] = Ybus[N2, N2] + YY + 1j * branch[k, 4]
        Ybus[N1, N2] = Ybus[N1, N2] - tap * YY
        Ybus[N2, N1] = Ybus[N2, N1] - tap * YY
    return Ybus


def Ybus_aumentada(system): 
    result = pypower.api.runpf(system)[0]
    Nbus = int(max([max(system['branch'][:, 0]), max(system['branch'][:, 1])]))
    NG   = system['gen'][:, 0]
    Ngen = len(NG)
    Nload = system['bus'][[4, 6, 8], 0]
    NumC = len(Nload)
    YbusB = CalYbus(system['branch'])
    Ybus = np.zeros([Nbus + Ngen, Nbus + Ngen])
    Ybus = np.complex_(Ybus)
    Ybus[0:Nbus, 0:Nbus] = YbusB
    Vn = np.zeros([3, 1])
    Vn = np.complex_(Vn)
    for k in range(Ngen):
        n = int(NG[k]) - 1
        kk = k + Nbus
        xd = system['gen'][k, 21]
        yd = 1/(1j*xd)
        Ybus[n, n] = Ybus[n, n] + yd
        Ybus[kk, kk] = Ybus[kk, kk] + yd
        Ybus[kk, n] = Ybus[kk, n] - yd
        Ybus[n, kk] = Ybus[n, kk] - yd
        # generator internal voltage
        Vbus = result['bus'][n, 7] * (np.cos(result['bus'][n, 7] * math.pi / 180) + 1j * np.sin(result['bus'][n, 8] * math.pi/180))
        I = np.conj((result['gen'][n, 1] + 1j * result['gen'][n, 2]) / 100 / Vbus)
        Vn[k, 0] = Vbus + 1j*xd*I

    # convert loads to impedances and include them in the Ybus
    for k in range(NumC):
        n = int(Nload[k]) - 1
        S = (result['bus'][n, 2] + 1j * result['bus'][n, 3]) / 100
        Vbus = result['bus'][n, 7] * (np.cos(result['bus'][n, 7] * math.pi / 180) + 1j * np.sin(result['bus'][n, 7] * math.pi / 180))
        V = abs(Vbus)
        Y = np.conj(S/(V*V))
        Ybus[n, n] = Ybus[n, n] + Y
    return Ybus, Vn


def  Ybus_reduction(Ybus, NN, NR):
    Yg = Ybus[NN:NN+NR, NN:NN+NR]
    Yb = Ybus[NN:NN+NR, 0:NN]
    Yc = Ybus[0:NN, NN:NN+NR]
    Ye = Ybus[0:NN, 0:NN]
    Ybusr = Yg - Yb@np.linalg.inv(Ye)@Yc
    return Ybusr


def fault(Ybus, fault_branch):
    bus = np.arange(0, 12, 1)
    if fault_branch == 1:
        fault_bus = 3
    if fault_branch == 4:
        fault_bus = 5
    if fault_branch == 5:
        fault_bus = 7
    Ybus_fault = np.delete(Ybus, fault_bus, 0)
    Ybus_fault = np.delete(Ybus_fault, fault_bus, 1)
    return Ybus_fault


def post_fault_Ybus(system, fault_branch, Ybus):
    Ybusx =Ybus
    N1 = int(system['branch'][fault_branch,0]-1)
    N2 = int(system['branch'][fault_branch,1]-1)
    YY = 1/(system['branch'][fault_branch,2]+1j*system['branch'][fault_branch,3])
    bkm = system['branch'][fault_branch,4]
    tap = 1.0
    if tap==0:
        tap = 1.0
    tap = 1/tap
    Ybusx[N1,N1] = Ybusx[N1,N1] - tap*tap*YY - 1j*bkm
    Ybusx[N2,N2] = Ybusx[N2,N2] - YY         - 1j*bkm
    Ybusx[N1,N2] = Ybusx[N1,N2] + tap*YY
    Ybusx[N2,N1] = Ybusx[N2,N1] + tap*YY
    return Ybusx


def post_fault(system, fault_branch):
    case_new = deepcopy(system)
    branch_new = np.delete(case_new['branch'], fault_branch, axis=0)
    case_new['branch'] = branch_new
    return case_new 


def cal_stability(power_system, fault_branch):
    system = pypower.api.runpf(power_system)[0]
    #Inertia values for generator
    M = 2 * np.array([23.64, 6.80, 3.01]) / (2 * math.pi * 50) 
    #time(s):[short_circuit, open_time]
    fault_time = [0.1, 0.6] #play around with this to see when the stability improves
    Pm = system['gen'][:, 1] / 100
    t = np.linspace(0, 10, 1001) #reduce this from 10 

    Ybus, Vn = Ybus_aumentada(system)
    Y_nofault = Ybus_reduction(Ybus, 9, 3)

    Ybus_fault = fault(Ybus, fault_branch)
    Y_fault = Ybus_reduction(Ybus_fault, 8, 3)

    system_post_fault = post_fault(system, fault_branch)
    Ybus_post_fault, _ = Ybus_aumentada(system_post_fault)
    Y_post_fault = Ybus_reduction(Ybus_post_fault, 9, 3)


    Y = {0: Y_nofault,
         1: Y_fault,
         2: Y_post_fault}
    x0 = np.hstack([np.transpose(np.angle(Vn)), np.mat([0, 0, 0])]).tolist()[0]
    V0 = np.transpose(np.abs(Vn)).tolist()[0]

    x = odeint(dx_dt, x0, t, args=(fault_time, Y, V0, Pm, M))

    MT = sum(M)
    xcoi = np.zeros([len(x), 3]) #rotor angle values
    d_max = np.zeros(len(x))
    for k in range(len(x)):
        d = sum(x[k, 0:3] * M) / MT
        # w = sum(x[k, 3:6] * M) / MT
        xcoi[k, :] = x[k, 0:3] - [d, d, d]
        d_max[k] = max(xcoi[k, :]) - min(xcoi[k, :])

    return xcoi, max(d_max)*180/math.pi


#load the excel as pandas dataframe
bus_loads_imag = pd.read_excel('IEEE9bus_loads.xlsx', header=None, sheet_name='loads_imag')
bus_loads_imag = bus_loads_imag*100
bus_loads_imag = round(bus_loads_imag,2)

bus_loads_real = pd.read_excel('IEEE9bus_loads.xlsx', header=None, sheet_name='loads_real')
bus_loads_real = bus_loads_real*100
bus_loads_real = round(bus_loads_real,2)

d_max = [] #if d_mx is >180 its unstable
xcoi = []

# for row in range(1000): 
# #This simulation is for a single load. Loop through all the loads to calculate the stability index
#     power_system = pypower.api.runpf(pypower.api.case9())[0]
#     #Active power on load buses
#     power_system['bus'][[4, 6, 8], 2] = [56.28, 43.16, 127.68] #replace these with the page 1 values 
#     #Reactive power on load buses
#     power_system['bus'][[4, 6, 8], 3] = [27.34, 33.77, 45.25] #replace these with the page 2 values

#     fault_branch = 5 #is this constant? #try changing to see what happens #focus on one fault usually 

#     xcoi_temp, d_max_temp = cal_stability(power_system, fault_branch)
#     d_max.append(d_max_temp)
#     xcoi.append(xcoi)

# print(d_max)




In [2]:
d_max

[]

In [3]:
xcoi

[]

In [4]:
stable_pnts = ([x for x in d_max if x<=180]) #stable points

In [5]:
indexes = []
for j in stable_pnts:
    indexes.append(d_max.index(j))

In [6]:
len(indexes)

0

In [14]:
stable_bus_loads_real = []
for i in indexes:
    stable_bus_loads_real.append([bus_loads_real[0][i], bus_loads_real[1][i], bus_loads_real[2][i]])

stable_bus_loads_real

549

In [16]:
stable_bus_loads_real = pd.DataFrame(stable_bus_loads_real)

In [17]:
stable_bus_loads_real

0       1       2
0     94.44  139.39  126.20
1     98.12  147.92  165.88
2     87.79  138.81  112.39
3    108.61  138.05   92.41
4    103.48  127.66  169.91
..      ...     ...     ...
544  123.45  123.08  145.18
545   64.24  108.04  162.63
546  132.70   73.26  167.36
547  127.30   81.87  128.36
548   69.49   98.46  132.15

[549 rows x 3 columns]

In [18]:
stable_bus_loads_imag = []
for i in indexes:
    stable_bus_loads_imag.append([bus_loads_imag[0][i], bus_loads_imag[1][i], bus_loads_imag[2][i]])

stable_bus_loads_imag = pd.DataFrame(stable_bus_loads_imag)

In [19]:
stable_bus_loads_imag

0      1      2
0    26.18  34.31  56.51
1    25.03  34.60  52.66
2    28.79  35.65  49.67
3    24.54  30.66  57.42
4    32.86  31.42  52.64
..     ...    ...    ...
544  26.12  37.34  55.18
545  25.47  40.88  56.49
546  30.40  37.64  44.41
547  26.83  32.83  47.05
548  24.32  41.66  50.44

[549 rows x 3 columns]

In [21]:
with pd.ExcelWriter('Stable_Loads.xlsx') as writer:  
    stable_bus_loads_real.to_excel(writer, sheet_name='loads_real', header=False, index=False)
    stable_bus_loads_imag.to_excel(writer, sheet_name='loads_imag', header=False, index=False)

In [23]:
unstable_bus_loads_real = bus_loads_real.drop(indexes)
unstable_bus_loads_imag = bus_loads_imag.drop(indexes)

In [24]:
with pd.ExcelWriter('Unstable_Loads.xlsx') as writer:  
    unstable_bus_loads_real.to_excel(writer, sheet_name='loads_real', header=False, index=False)
    unstable_bus_loads_imag.to_excel(writer, sheet_name='loads_imag', header=False, index=False)

#  TEST UNSTABLE POINTS

In [7]:
unstable_bus_loads_gen1 = pd.read_excel('Unstable2s_Points_Gen.xlsx', sheet_name='gen1')
unstable_bus_loads_gen2 = pd.read_excel('Unstable2s_Points_Gen.xlsx', sheet_name='gen2')
unstable_bus_loads_gen3 = pd.read_excel('Unstable2s_Points_Gen.xlsx', sheet_name='gen3')
unstable_bus_loads_gen1

Rotor Angle  Active Power  Voltage Mag  stable  Rotor Angle (scaled)  \
0       0.830240         85.48     0.980714       0              0.014352   
1       0.821467         91.98     0.979973       0              0.012793   
2       0.852572         59.66     0.977993       0              0.018320   
3       0.838266         75.40     0.986590       0              0.015778   
4       0.832825         51.31     0.992769       0              0.014811   
..           ...           ...          ...     ...                   ...   
446     0.833812         56.60     0.990453       0              0.014986   
447     0.865821         47.14     0.988251       0              0.020674   
448     0.823282         93.84     0.975624       0              0.013115   
449     0.767698        124.96     0.974978       0              0.003238   
450     0.810004        106.52     0.978015       0              0.010756   

     Voltage Mag (scaled)  Predicted Active Power scaled  
0                0.538205                      88.916854  
1                0.515481                      93.306106  
2                0.454812                     103.217275  
3                0.718272                      26.491231  
4                0.907658                    -117.031812  
..                    ...                            ...  
446              0.836671                     -51.315309  
447              0.769193                      -0.822221  
448              0.382193                     110.146856  
449              0.362414                     111.173444  
450              0.455484                     102.605382  

[451 rows x 7 columns]

In [8]:
unstable_bus_loads_imag = pd.read_excel('Unstable_Loads.xlsx', header=None, sheet_name='loads_imag')
unstable_bus_loads_imag

0      1      2
0    32.18  36.54  42.93
1    32.16  29.08  49.18
2    34.25  38.35  51.24
3    27.34  33.77  45.25
4    25.95  40.77  40.47
..     ...    ...    ...
446  24.98  35.43  49.42
447  34.02  40.25  41.24
448  31.61  28.54  58.28
449  24.77  41.20  58.39
450  31.16  37.96  44.35

[451 rows x 3 columns]

In [9]:
unstable_pred_AP = []

for e in range (len(unstable_bus_loads_gen1['Predicted Active Power scaled'])):
    unstable_pred_AP.append([unstable_bus_loads_gen1['Predicted Active Power scaled'][e], unstable_bus_loads_gen2['Predicted Active Power scaled'][e], unstable_bus_loads_gen3['Predicted Active Power scaled'][e]])

unstable_pred_AP


[[88.91685352632851, 126.4717125650799, 165.1633225224696],
 [93.30610580454743, 116.4206466026453, 163.4181241465153],
 [103.2172745908517, 126.4846697139608, 169.193602099872],
 [26.49123074752663, 119.0156035164892, 164.6580754151267],
 [-117.0318119053667, 129.2401313900736, 158.8052110718643],
 [97.40918931788553, 129.0468853837192, 168.5359333568931],
 [86.4085730285509, 128.2749940089005, 164.087665870268],
 [82.91284852082015, 128.6520070842589, 166.0559349869334],
 [99.03956922646, 123.7855380834733, 167.2064233214592],
 [25.84159514230907, 127.1030784161203, 160.8072720388994],
 [98.72267489921626, 127.988011744147, 168.8236189656686],
 [56.11810510506541, 128.3401810565964, 168.3094664903236],
 [63.74252293021493, 129.0888218603388, 169.1457071134738],
 [116.7108114526796, 120.7345184436395, 167.7326419227644],
 [91.64748165241338, 126.646954245791, 169.1753773065368],
 [33.73111134840894, 128.183247797552, 167.8936269072749],
 [45.26164239513366, 119.6936379744292, 159.3706

In [10]:
unstable_bus_loads_imag[1][1]

29.08

In [11]:
d_max = [] #if d_mx is >180 its unstable
xcoi = []

for row in range(451): 
#This simulation is for a single load. Loop through all the loads to calculate the stability index
    power_system = pypower.api.runpf(pypower.api.case9())[0]
    #Active power on load buses
    power_system['bus'][[4, 6, 8], 2] = [unstable_pred_AP[row][0], unstable_pred_AP[row][1], unstable_pred_AP[row][2]] #replace these with the page 1 values 
    #Reactive power on load buses
    power_system['bus'][[4, 6, 8], 3] = [unstable_bus_loads_imag[0][row], unstable_bus_loads_imag[1][row], unstable_bus_loads_imag[2][row]] #replace these with the page 2 values

    fault_branch = 5 #is this constant? #try changing to see what happens #focus on one fault usually 

    xcoi_temp, d_max_temp = cal_stability(power_system, fault_branch)
    d_max.append(d_max_temp)
    xcoi.append(xcoi)

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.04 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.03 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.03 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 


Newton's method power flow converged in 4 iterations.

Converged in 0.03 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch Charging (inj)     -              132.2
Inter-ties         0   

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.03 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    176.3              18.7
Loads              3     Load                   171.0             107.2
  Fixed            3       Fixed                171.0             107.2
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         5.32             44.86
Transformers       0     Branch 

...

    7  0.983   -6.566       -         -      127.41     35.43 
    8  0.995   -5.106       -         -         -         -   
    9  0.959   -9.057       -         -      167.82     49.42 
                        --------  --------  --------  --------
               Total:    247.86     19.06    243.92    109.83

|     Branch Data                                                              |
Brnch   From   To    From Bus Injection   To Bus Injection     Loss (I^2 * Z)  
  #     Bus    Bus    P (MW)   Q (MVAr)   P (MW)   Q (MVAr)   P (MW)   Q (MVAr)
-----  -----  -----  --------  --------  --------  --------  --------  --------
   0      1      4     82.86     15.72    -82.86    -11.63     0.007      4.10
   1      4      5    -43.54    -10.02     43.87     -3.91     0.328      1.78
   2      5      6      7.44    -21.07     -7.42    -14.88     0.025      0.11
   3      3      6     85.00     -6.21    -84.99     10.46     0.007      4.26
   4      6      7     92.41      4.41    -91.38


Converged in 0.02 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    263.6              16.6
Loads              3     Load                   261.1             115.5
  Fixed            3       Fixed                261.1             115.5
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.55             34.07
Transformers       0     Branch Charging (inj)     -              133.0
Inter-ties         0     Total Inter-tie Flow     0.0               0.0
Areas 


Newton's method power flow converged in 3 iterations.

Converged in 0.02 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    402.7              69.1
Loads              3     Load                   397.4             118.4
  Fixed            3       Fixed                397.4             118.4
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         5.37             80.25
Transformers       0     Branch Charging (inj)     -              129.6
Inter-ties         0   

    7  0.987   -8.601       -         -      100.00     35.00 
    8  0.997   -6.716       -         -         -         -   
    9  0.964   -9.686       -         -      125.00     50.00 
                        --------  --------  --------  --------
               Total:    317.98     24.80    315.00    115.00

|     Branch Data                                                              |
Brnch   From   To    From Bus Injection   To Bus Injection     Loss (I^2 * Z)  
  #     Bus    Bus    P (MW)   Q (MVAr)   P (MW)   Q (MVAr)   P (MW)   Q (MVAr)
-----  -----  -----  --------  --------  --------  --------  --------  --------
   0      1      4    152.98     22.98   -152.96     -9.19     0.024     13.78
   1      4      5     60.42     -5.35    -59.79     -6.56     0.634      3.43
   2      5      6    -30.21    -23.44     30.60    -10.08     0.387      1.69
   3      3      6     85.00     -4.30    -84.99      8.54     0.007      4.24
   4      6      7     54.39      1.53    -54.03


Newton's method power flow converged in 4 iterations.

Converged in 0.02 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch Charging (inj)     -              132.2
Inter-ties         0   

In [12]:
len(d_max)

451

In [13]:
stable_pnts = ([x for x in d_max if x<=180]) #stable points

In [14]:
len(stable_pnts)

359

In [15]:
indexes = []
for j in stable_pnts:
    indexes.append(d_max.index(j))

In [16]:
len(indexes)

359

In [17]:
indexes

[0,
 1,
 2,
 3,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 22,
 23,
 24,
 25,
 26,
 28,
 29,
 31,
 32,
 33,
 35,
 37,
 38,
 39,
 40,
 41,
 42,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 51,
 52,
 53,
 54,
 56,
 57,
 59,
 60,
 61,
 62,
 64,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 81,
 84,
 86,
 87,
 88,
 89,
 90,
 92,
 93,
 94,
 95,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 108,
 109,
 111,
 112,
 113,
 114,
 116,
 118,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 130,
 131,
 132,
 133,
 134,
 136,
 137,
 138,
 139,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 149,
 150,
 151,
 152,
 153,
 155,
 156,
 157,
 158,
 159,
 160,
 161,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 174,
 175,
 176,
 177,
 178,
 179,
 181,
 182,
 183,
 184,
 186,
 187,
 188,
 189,
 190,
 191,
 192,
 193,
 194,
 195,
 197,
 198,
 200,
 201,
 202,
 203,
 205,
 206,
 207,
 208,
 210,
 211,
 213,
 214,
 215,
 216,
 218,
 219,
 220,
 2

In [49]:
unstable_bus_loads_gen1 = unstable_bus_loads_gen1.drop(columns=['stabilised'])

In [50]:
unstable_bus_loads_gen1

Rotor Angle  Active Power  Voltage Mag  stable  Predicted Active Power
0       0.991842         85.48     0.980714       0               81.892563
1       4.012295         91.98     0.979973       0           -81343.045205
2       1.101612         59.66     0.977993       0               80.580261
3       1.098730         75.40     0.986590       0               56.275415
4       0.990676         51.31     0.992769       0               45.516743
..           ...           ...          ...     ...                     ...
446     0.984957         56.60     0.990453       0               52.730384
447     1.115297         47.14     0.988251       0               48.955312
448     1.067474         93.84     0.975624       0               91.736990
449     0.895542        124.96     0.974978       0               98.861040
450     0.961468        106.52     0.978015       0               90.424650

[451 rows x 5 columns]

In [14]:
unstable_bus_loads_gen1['stabilised scaled'] = 0

for j in range (len(unstable_bus_loads_gen1['Predicted Active Power scaled'])):
    if j in indexes:
        unstable_bus_loads_gen1['stabilised scaled'][j] = int(1)
    else:
        unstable_bus_loads_gen1['stabilised scaled'][j] = int(0)
        
unstable_bus_loads_gen1

<ipython-input-14-97ac188d9ab8>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  unstable_bus_loads_gen1['stabilised scaled'][j] = int(1)
<ipython-input-14-97ac188d9ab8>:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  unstable_bus_loads_gen1['stabilised scaled'][j] = int(0)


Rotor Angle  Active Power  Voltage Mag  stable  Predicted Active Power  \
0       0.991842         85.48     0.980714       0               81.892563   
1       4.012295         91.98     0.979973       0           -81343.045205   
2       1.101612         59.66     0.977993       0               80.580261   
3       1.098730         75.40     0.986590       0               56.275415   
4       0.990676         51.31     0.992769       0               45.516743   
..           ...           ...          ...     ...                     ...   
446     0.984957         56.60     0.990453       0               52.730384   
447     1.115297         47.14     0.988251       0               48.955312   
448     1.067474         93.84     0.975624       0               91.736990   
449     0.895542        124.96     0.974978       0               98.861040   
450     0.961468        106.52     0.978015       0               90.424650   

     stabilised  Rotor Angle (scaled)  Voltage Mag (scaled)  \
0             0              0.000580              0.538205   
1             0              0.013457              0.515481   
2             1              0.001048              0.454812   
3             0              0.001036              0.718272   
4             0              0.000575              0.907658   
..          ...                   ...                   ...   
446           0              0.000551              0.836671   
447           1              0.001107              0.769193   
448           1              0.000903              0.382193   
449           1              0.000170              0.362414   
450           1              0.000451              0.455484   

     Predicted Active Power scaled  stabilised scaled  
0                        87.283832                  1  
1                        93.373914                  1  
2                       101.996818                  1  
3                        22.320791                  1  
4                      -125.202688                  0  
..                             ...                ...  
446                     -57.796094                  0  
447                      -7.592526                  0  
448                     109.632185                  1  
449                     111.060627                  1  
450                     101.862721                  1  

[451 rows x 10 columns]

In [15]:
count_1=0
count_0=0
for j in range (len(unstable_bus_loads_gen1['Predicted Active Power'])):
    if unstable_bus_loads_gen1['Predicted Active Power scaled'][j] < 0:
        if unstable_bus_loads_gen1['stabilised scaled'][j] == 1:
            count_1 +=1
        else:
            count_0 +=1
print(count_1)
print(count_0)

0
54


In [16]:
with pd.ExcelWriter('Unstable_Points_Gen.xlsx') as writer:  
    unstable_bus_loads_gen1.to_excel(writer, sheet_name='gen1', header=True, index=False)
    unstable_bus_loads_gen2.to_excel(writer, sheet_name='gen2', header=True, index=False)
    unstable_bus_loads_gen3.to_excel(writer, sheet_name='gen3', header=True, index=False)
#     unstable_bus_loads_imag.to_excel(writer, sheet_name='loads_imag', header=False, index=False)